In [3]:
import pandas as pd
import numpy as np
from sklearn.tree import DecisionTreeClassifier, plot_tree
from sklearn.model_selection import GroupShuffleSplit, cross_validate, cross_val_score, StratifiedKFold
from sklearn.metrics import make_scorer, precision_score, recall_score
import matplotlib.pyplot as plt

ValueError: Key backend: 'module://matplotlib_inline.backend_inline' is not a valid value for backend; supported values are ['gtk3agg', 'gtk3cairo', 'gtk4agg', 'gtk4cairo', 'macosx', 'nbagg', 'notebook', 'qtagg', 'qtcairo', 'qt5agg', 'qt5cairo', 'tkagg', 'tkcairo', 'webagg', 'wx', 'wxagg', 'wxcairo', 'agg', 'cairo', 'pdf', 'pgf', 'ps', 'svg', 'template']

In [4]:
df = pd.read_csv('../../data/answerList_data.csv')
df['correctness'] = (((df['Ground_Truth'] == 0.0) & (df['Answer.option'] == 'NO')) | ((df['Ground_Truth'] == 1.0) & (df['Answer.option'] == 'YES'))).astype(int)

df

Answer.ID FailingMethod  Question.ID  Answer.duration  \
0           261       HIT01_8            0           90.984   
1           262       HIT01_8            0          133.711   
2           263       HIT01_8            0           77.696   
3           264       HIT01_8            0           46.644   
4           265       HIT01_8            0          215.416   
...         ...           ...          ...              ...   
2575       2316      HIT08_54          128          220.420   
2576       2317      HIT08_54          128          322.790   
2577       2318      HIT08_54          128          159.530   
2578       2319      HIT08_54          128           68.578   
2579       2320      HIT08_54          128           72.605   

      Answer.confidence  Answer.difficulty  Ground_Truth  TP  TN  FN  ...  \
0                     4                  2           0.0   0   1   0  ...   
1                     5                  1           0.0   0   1   0  ...   
2                     5                  2           0.0   0   1   0  ...   
3                     1                  1           0.0   0   1   0  ...   
4                     5                  5           0.0   0   1   0  ...   
...                 ...                ...           ...  ..  ..  ..  ...   
2575                  2                  4           0.0   0   1   0  ...   
2576                  4                  3           0.0   0   0   0  ...   
2577                  5                  1           0.0   0   1   0  ...   
2578                  5                  1           0.0   0   1   0  ...   
2579                  4                  4           0.0   0   1   0  ...   

                                      Worker.ID Worker.score  \
0                 832cg-7G1i-462:73eI-8E-2g-985            5   
1                                 98ce7A-4i-507            4   
2                  881AC0I2E-625:135cI3E-7e8-86            5   
3                270eG-5c6A3-46:65eI-2i-2I-9-36            5   
4                  844Cg1g5e1-17:255ei-8G8E85-8            3   
...                                         ...          ...   
2575                          1171ea-4g-6C-73-8            3   
2576             66AC-5a0g-47-9:1443IA-7C-6e967            5   
2577           106iG8G-9I-9-80:590CG-6G-7i-71-9            4   
2578  1221iC8A5A242:495CC9e6a691:11aE2c-4c-9-86            4   
2579                 1520Ea3c0E3-65:9AI0g4a-386            5   

           Worker.profession Worker.yearsOfExperience  Worker.age  \
0      Undergraduate_Student                      7.0          21   
1      Undergraduate_Student                     10.0          25   
2     Professional_Developer                      7.0          24   
3     Professional_Developer                     20.0          38   
4      Undergraduate_Student                      5.0          19   
...                      ...                      ...         ...   
2575        Graduate_Student                      2.0          28   
2576  Professional_Developer                     17.0          39   
2577  Professional_Developer                     10.0          31   
2578   Undergraduate_Student                      4.0          19   
2579        Graduate_Student                      3.0          24   

      Worker.gender                Worker.whereLearnedToCode  Worker.country  \
0              Male                              High School   United States   
1            Female               High School;University;Web   United States   
2              Male               High School;University;Web   United States   
3              Male  High School;University;Other On the job             USA   
4              Male               High School;University;Web   United States   
...             ...                                      ...             ...   
2575           Male                               University             USA   
2576           Male                           University;Web             USA   
2577  

In [5]:
def calculate_ttr(text):
    tokens = text.split()
    unique_tokens = set(tokens)
    ttr = len(unique_tokens) / len(tokens) if tokens else 0
    return ttr

df['TTR'] = df['Answer.explanation'].astype(str).apply(calculate_ttr)
df

Answer.ID FailingMethod  Question.ID  Answer.duration  \
0           261       HIT01_8            0           90.984   
1           262       HIT01_8            0          133.711   
2           263       HIT01_8            0           77.696   
3           264       HIT01_8            0           46.644   
4           265       HIT01_8            0          215.416   
...         ...           ...          ...              ...   
2575       2316      HIT08_54          128          220.420   
2576       2317      HIT08_54          128          322.790   
2577       2318      HIT08_54          128          159.530   
2578       2319      HIT08_54          128           68.578   
2579       2320      HIT08_54          128           72.605   

      Answer.confidence  Answer.difficulty  Ground_Truth  TP  TN  FN  ...  \
0                     4                  2           0.0   0   1   0  ...   
1                     5                  1           0.0   0   1   0  ...   
2                     5                  2           0.0   0   1   0  ...   
3                     1                  1           0.0   0   1   0  ...   
4                     5                  5           0.0   0   1   0  ...   
...                 ...                ...           ...  ..  ..  ..  ...   
2575                  2                  4           0.0   0   1   0  ...   
2576                  4                  3           0.0   0   0   0  ...   
2577                  5                  1           0.0   0   1   0  ...   
2578                  5                  1           0.0   0   1   0  ...   
2579                  4                  4           0.0   0   1   0  ...   

      Worker.score       Worker.profession  Worker.yearsOfExperience  \
0                5   Undergraduate_Student                       7.0   
1                4   Undergraduate_Student                      10.0   
2                5  Professional_Developer                       7.0   
3                5  Professional_Developer                      20.0   
4                3   Undergraduate_Student                       5.0   
...            ...                     ...                       ...   
2575             3        Graduate_Student                       2.0   
2576             5  Professional_Developer                      17.0   
2577             4  Professional_Developer                      10.0   
2578             4   Undergraduate_Student                       4.0   
2579             5        Graduate_Student                       3.0   

     Worker.age  Worker.gender                Worker.whereLearnedToCode  \
0            21           Male                              High School   
1            25         Female               High School;University;Web   
2            24           Male               High School;University;Web   
3            38           Male  High School;University;Other On the job   
4            19           Male               High School;University;Web   
...         ...            ...                                      ...   
2575         28           Male                               University   
2576         39           Male                           University;Web   
2577         31           Male    High School;University;Web;Other work   
2578         19           Male      University;Web;Other FIRST Robotics   
2579         24           Male                           University;Web   

     Worker.country  Worker.programmingLanguage correctness       TTR  
0     United States               Java; C++; C#           1  0.937500  
1     United States                          c#           1  0.923077  
2     United States                C++;Java;PHP           1  0.827586  
3               USA                          C#           1  1.000000  
4     United States                   C++; Java           1  0.941176  
...             ...                         ...         ...       ...  
2575            USA                          C#       

In [6]:
df['Answer.option.int'] = df['Answer.option'].map({'NO': 0, 'IDK': 0.5, 'YES': 1})
df['Worker.gender.int'] = df['Worker.gender'].map({'Male': -1, 'Other': 0, 'Female': 1})


In [7]:
df_holdout = df[df['FailingMethod'].isin(['HIT01_8', 'HIT02_24'])]
df_train = df[~df['FailingMethod'].isin(['HIT01_8', 'HIT02_24'])]

df_train

Answer.ID FailingMethod  Question.ID  Answer.duration  \
320         621       HIT03_6           16          225.484   
321         622       HIT03_6           16           75.758   
322         623       HIT03_6           16          396.716   
323         624       HIT03_6           16          899.377   
324         625       HIT03_6           16          253.272   
...         ...           ...          ...              ...   
2575       2316      HIT08_54          128          220.420   
2576       2317      HIT08_54          128          322.790   
2577       2318      HIT08_54          128          159.530   
2578       2319      HIT08_54          128           68.578   
2579       2320      HIT08_54          128           72.605   

      Answer.confidence  Answer.difficulty  Ground_Truth  TP  TN  FN  ...  \
320                   4                  2           0.0   0   1   0  ...   
321                   5                  2           0.0   0   1   0  ...   
322                   5                  2           0.0   0   0   0  ...   
323                   4                  3           0.0   0   1   0  ...   
324                   0                  5           0.0   0   0   0  ...   
...                 ...                ...           ...  ..  ..  ..  ...   
2575                  2                  4           0.0   0   1   0  ...   
2576                  4                  3           0.0   0   0   0  ...   
2577                  5                  1           0.0   0   1   0  ...   
2578                  5                  1           0.0   0   1   0  ...   
2579                  4                  4           0.0   0   1   0  ...   

      Worker.yearsOfExperience Worker.age  Worker.gender  \
320                       20.0         35           Male   
321                        5.0         26           Male   
322                       10.0         33           Male   
323                        5.0         33           Male   
324                        3.0         49         Female   
...                        ...        ...            ...   
2575                       2.0         28           Male   
2576                      17.0         39           Male   
2577                      10.0         31           Male   
2578                       4.0         19           Male   
2579                       3.0         24           Male   

                  Worker.whereLearnedToCode  Worker.country  \
320                  High School;University              US   
321                  High School;University             USA   
322                              University   United States   
323                          University;Web             USA   
324                              University              US   
...                                     ...             ...   
2575                             University             USA   
2576                         University;Web             USA   
2577  High School;University;Web;Other work             usa   
2578    University;Web;Other FIRST Robotics   United States   
2579                         University;Web           India   

      Worker.programmingLanguage correctness       TTR Answer.option.int  \
320                          c++           1  0.875000               0.0   
321                         Java           1  0.708333               0.0   
322                         Java           0  0.576923               1.0   
323                   matlab; js           1  1.000000               0.0   
324                          php           0  1.000000               0.5   
...                          ...         ...       ...               ...   
2575                          C#           1  0.766667               0.0   
2576            C#; VB.NET; Java           0  0.928571               1.0   
2577                         C++           1  1.000000               0.0   
2578                         C++           1  1.000000               0.0   
2579      

## First Tree: Decision Tree Classifier

In [8]:
input_cols_full = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.profession', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
input_cols = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
output_col = 'correctness'

X = df_train[input_cols]
y = df_train[output_col]

groups = df_train['FailingMethod'].values
gss = GroupShuffleSplit(n_splits=len(pd.unique(groups)), test_size=1/len(pd.unique(groups)))

In [16]:
clf = DecisionTreeClassifier(random_state=42)


precision_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='precision')
recall_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='recall')

print("Precision for each group split:", precision_scores)
print("Mean Precision:", np.mean(precision_scores))

print("Recall for each group split:", recall_scores)
print("Mean Recall:", np.mean(recall_scores))


Precision for each group split: [0.81415929 0.64835165 0.79910714 0.64835165 0.81748072 0.79910714]
Mean Precision: 0.7544262657078876
Recall for each group split: [0.80630631 0.80630631 0.62765957 0.76963351 0.78632479 0.78632479]
Mean Recall: 0.7637592112639456


In [10]:
clf = DecisionTreeClassifier()

cv_results = cross_validate(
    clf, X, y, cv=gss, groups=groups,
    scoring=['precision', 'recall'],
    return_estimator=True
)

print("Precision for each fold:", cv_results['test_precision'])
print("Mean Precision:", np.mean(cv_results['test_precision']))

print("Recall for each fold:", cv_results['test_recall'])
print("Mean Recall:", np.mean(cv_results['test_recall']))


best_model_idx = np.argmax(cv_results['test_precision'])
best_model = cv_results['estimator'][best_model_idx]

Precision for each fold: [0.79555556 0.81794872 0.65957447 0.81165919 0.8        0.82142857]
Mean Precision: 0.7843610843071772
Recall for each fold: [0.80630631 0.71846847 0.65957447 0.81531532 0.81081081 0.78632479]
Mean Recall: 0.7661333592184656


In [69]:
plt.figure(figsize=(200, 100))
plot_tree(best_model, filled=True, feature_names=input_cols, class_names=np.unique(y).astype(str), rounded=True, fontsize=9)
plt.title("Decision Tree of Best Model Based on Precision")
plt.show()

## Second Tree: Gradient Boosted Decision Tree

Increase precision from average 0.775 to 0,82

In [21]:
from sklearn.ensemble import GradientBoostingClassifier


input_cols_full = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.profession', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
input_cols = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
output_col = 'correctness'

X = df_train[input_cols]
y = df_train[output_col]

groups = df_train['FailingMethod'].values
gss = GroupShuffleSplit(n_splits=len(pd.unique(groups)), test_size=1/len(pd.unique(groups)))

clf = GradientBoostingClassifier(random_state=42)


precision_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='precision')
recall_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='recall')

print("Precision for each group split:", precision_scores)
print("Mean Precision:", np.mean(precision_scores))

print("Recall for each group split:", recall_scores)
print("Mean Recall:", np.mean(recall_scores))


Precision for each group split: [0.68965517 0.7970297  0.83739837 0.83739837 0.87935657 0.87935657]
Mean Precision: 0.8200324600134654
Recall for each group split: [0.84293194 0.93447293 0.84293194 0.63829787 0.92792793 0.63829787]
Mean Recall: 0.8041434135712104


## Third Tree: Minimal number of input columns
Very high recall but low precision --> many positives (false and true)

In [24]:
from sklearn.ensemble import GradientBoostingClassifier


input_cols_full = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.profession', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
input_cols = ['Answer.confidence', 'Answer.difficulty', 'Worker.score', 'Worker.yearsOfExperience']
output_col = 'correctness'

X = df_train[input_cols]
y = df_train[output_col]

groups = df_train['FailingMethod'].values
gss = GroupShuffleSplit(n_splits=len(pd.unique(groups)), test_size=1/len(pd.unique(groups)))

clf = GradientBoostingClassifier(random_state=42)


precision_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='precision')
recall_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='recall')

print("Precision for each group split:", precision_scores)
print("Mean Precision:", np.mean(precision_scores))

print("Recall for each group split:", recall_scores)
print("Mean Recall:", np.mean(recall_scores))


Precision for each group split: [0.67808219 0.67647059 0.58333333 0.76888889 0.58333333 0.73508772]
Mean Precision: 0.6708660091449863
Recall for each group split: [0.94369369 0.96335079 0.94369369 0.94369369 0.98648649 0.96335079]
Mean Recall: 0.9573781897080327


In [28]:
df_train

Answer.ID FailingMethod  Question.ID  Answer.duration  \
320         621       HIT03_6           16          225.484   
321         622       HIT03_6           16           75.758   
322         623       HIT03_6           16          396.716   
323         624       HIT03_6           16          899.377   
324         625       HIT03_6           16          253.272   
...         ...           ...          ...              ...   
2575       2316      HIT08_54          128          220.420   
2576       2317      HIT08_54          128          322.790   
2577       2318      HIT08_54          128          159.530   
2578       2319      HIT08_54          128           68.578   
2579       2320      HIT08_54          128           72.605   

      Answer.confidence  Answer.difficulty  Ground_Truth  TP  TN  FN  ...  \
320                   4                  2           0.0   0   1   0  ...   
321                   5                  2           0.0   0   1   0  ...   
322                   5                  2           0.0   0   0   0  ...   
323                   4                  3           0.0   0   1   0  ...   
324                   0                  5           0.0   0   0   0  ...   
...                 ...                ...           ...  ..  ..  ..  ...   
2575                  2                  4           0.0   0   1   0  ...   
2576                  4                  3           0.0   0   0   0  ...   
2577                  5                  1           0.0   0   1   0  ...   
2578                  5                  1           0.0   0   1   0  ...   
2579                  4                  4           0.0   0   1   0  ...   

      Worker.yearsOfExperience Worker.age  Worker.gender  \
320                       20.0         35           Male   
321                        5.0         26           Male   
322                       10.0         33           Male   
323                        5.0         33           Male   
324                        3.0         49         Female   
...                        ...        ...            ...   
2575                       2.0         28           Male   
2576                      17.0         39           Male   
2577                      10.0         31           Male   
2578                       4.0         19           Male   
2579                       3.0         24           Male   

                  Worker.whereLearnedToCode  Worker.country  \
320                  High School;University              US   
321                  High School;University             USA   
322                              University   United States   
323                          University;Web             USA   
324                              University              US   
...                                     ...             ...   
2575                             University             USA   
2576                         University;Web             USA   
2577  High School;University;Web;Other work             usa   
2578    University;Web;Other FIRST Robotics   United States   
2579                         University;Web           India   

      Worker.programmingLanguage correctness       TTR Answer.option.int  \
320                          c++           1  0.875000               0.0   
321                         Java           1  0.708333               0.0   
322                         Java           0  0.576923               1.0   
323                   matlab; js           1  1.000000               0.0   
324                          php           0  1.000000               0.5   
...                          ...         ...       ...               ...   
2575                          C#           1  0.766667               0.0   
2576            C#; VB.NET; Java           0  0.928571               1.0   
2577                         C++           1  1.000000               0.0   
2578                         C++           1  1.000000               0.0   
2579      

Adding the workers' professions somehow makes it worse. Maybe I did something wrong here.

In [35]:
df_train['Worker.profession.int'] = df_train['Worker.profession'].map({'Other': 0, 'Hobbyist': 1, 'Undergraduate_Student': 2, 'Graduate_Student': 3, 'Professional_Developer':4})
df_train

/var/folders/r0/mt3w6g5d6tn6cn8qq8dg8zrw0000gn/T/ipykernel_73823/2576780986.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_train['Worker.profession.int'] = df_train['Worker.profession'].map({'Other': 0, 'Hobbyist': 1, 'Undergraduate_Student': 2, 'Graduate_Student': 3, 'Professional_Developer':4})


Answer.ID FailingMethod  Question.ID  Answer.duration  \
320         621       HIT03_6           16          225.484   
321         622       HIT03_6           16           75.758   
322         623       HIT03_6           16          396.716   
323         624       HIT03_6           16          899.377   
324         625       HIT03_6           16          253.272   
...         ...           ...          ...              ...   
2575       2316      HIT08_54          128          220.420   
2576       2317      HIT08_54          128          322.790   
2577       2318      HIT08_54          128          159.530   
2578       2319      HIT08_54          128           68.578   
2579       2320      HIT08_54          128           72.605   

      Answer.confidence  Answer.difficulty  Ground_Truth  TP  TN  FN  ...  \
320                   4                  2           0.0   0   1   0  ...   
321                   5                  2           0.0   0   1   0  ...   
322                   5                  2           0.0   0   0   0  ...   
323                   4                  3           0.0   0   1   0  ...   
324                   0                  5           0.0   0   0   0  ...   
...                 ...                ...           ...  ..  ..  ..  ...   
2575                  2                  4           0.0   0   1   0  ...   
2576                  4                  3           0.0   0   0   0  ...   
2577                  5                  1           0.0   0   1   0  ...   
2578                  5                  1           0.0   0   1   0  ...   
2579                  4                  4           0.0   0   1   0  ...   

      Worker.age Worker.gender              Worker.whereLearnedToCode  \
320           35          Male                 High School;University   
321           26          Male                 High School;University   
322           33          Male                             University   
323           33          Male                         University;Web   
324           49        Female                             University   
...          ...           ...                                    ...   
2575          28          Male                             University   
2576          39          Male                         University;Web   
2577          31          Male  High School;University;Web;Other work   
2578          19          Male    University;Web;Other FIRST Robotics   
2579          24          Male                         University;Web   

     Worker.country  Worker.programmingLanguage  correctness       TTR  \
320              US                         c++            1  0.875000   
321             USA                        Java            1  0.708333   
322   United States                        Java            0  0.576923   
323             USA                  matlab; js            1  1.000000   
324              US                         php            0  1.000000   
...             ...                         ...          ...       ...   
2575            USA                          C#            1  0.766667   
2576            USA            C#; VB.NET; Java            0  0.928571   
2577            usa                         C++            1  1.000000   
2578  United States                         C++            1  1.000000   
2579          India                        Java            1  0.875000   

      Answer.option.int Worker.gender.int  Worker.profession.int  
320                 0.0                -1                      0  
321                 0.0                -1                      3  
322                 1.0                -1                      4  
323                 0.0                -1                      1  
324                 0.5                 1                      2  
...                 ...               ...                    ...  
2575                0.0                -1                      3  
2576                1.

In [34]:
from sklearn.ensemble import GradientBoostingClassifier


input_cols_full = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.profession', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
input_cols = ['Answer.duration', 'Answer.confidence', 'Answer.difficulty', 'Answer.option.int', 'Answer.order', 'Worker.score', 'Worker.yearsOfExperience', 'Worker.age', 'Worker.gender.int', 'TTR']
output_col = 'correctness'

X = df_train[input_cols]
y = df_train[output_col]

groups = df_train['FailingMethod'].values
gss = GroupShuffleSplit(n_splits=len(pd.unique(groups)), test_size=1/len(pd.unique(groups)))

clf = GradientBoostingClassifier(random_state=42)


precision_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='precision')
recall_scores = cross_val_score(clf, X, y, cv=gss, groups=groups, scoring='recall')

print("Precision for each group split:", precision_scores)
print("Mean Precision:", np.mean(precision_scores))

print("Recall for each group split:", recall_scores)
print("Mean Recall:", np.mean(recall_scores))


Precision for each group split: [0.87935657 0.7970297  0.7970297  0.7970297  0.90045249 0.90045249]
Mean Precision: 0.8452251091085116
Recall for each group split: [0.84293194 0.93447293 0.92792793 0.92792793 0.77777778 0.63829787]
Mean Recall: 0.841556062936628


## TODO

- education mit einbeziehen
- parameter reduzieren
- pruning, tiefe begrenzen
- gradient boosted decision tree
- TTR metrik austauschen
-